In [2]:
import os
import sys
import shutil
import numpy as np
sys.path.insert(0, '../scripts')

from eeg_cnn_lib import transfer_all_class, prepare_data_labels
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, f1_score, precision_score, confusion_matrix
from keras.preprocessing.image import ImageDataGenerator
from keras.models import Sequential
from keras.layers import Conv2D, MaxPooling2D
from keras.layers import Activation, Flatten, Dense, Dropout
from keras import optimizers

# The images are in a folder named 'shapes/training'
train_dir_name = '../../../data/classification/arousal/train'
validation_dir_name = '../../../data/classification/arousal/validation'
test_dir_name = '../../../data/classification/arousal/test'


# All images are 32 pixels
img_size = (32,32)
img_size_rgba = (32,32,4)

# The folder contains a subfolder for each class of shape
classes = sorted(os.listdir(train_dir_name))

Using TensorFlow backend.


In [3]:
transfer_all_class(test_dir_name,train_dir_name,1.0,classes)
transfer_all_class(validation_dir_name,train_dir_name,1.0,classes)
transfer_all_class(train_dir_name,test_dir_name,0.1,classes)



In [4]:
import sys
print(sys.executable)
print(sys.version)

/home/paulina/emotion-recognition/bin/python
3.7.7 (default, Apr 18 2020, 02:59:53) 
[GCC 9.3.0]


In [4]:
X, Y = prepare_data_labels(classes, train_dir_name)
X=np.asarray(X)
Y=np.asarray(Y)

In [5]:
X, Y = prepare_data_labels(classes, train_dir_name)
X=np.asarray(X)
Y=np.asarray(Y)

In [6]:
model = Sequential()

model.add(Conv2D(32, (3, 3), strides=1, padding='same', input_shape=img_size_rgba, activation='relu'))

model.add(MaxPooling2D(pool_size=(2,2),strides=2))

model.add(Conv2D(64, (3, 3), strides=1, padding='same', input_shape=img_size_rgba, activation='relu'))

model.add(MaxPooling2D(pool_size=(2,2),strides=2))

model.add(Conv2D(128, (3, 3), strides=1, padding='same', input_shape=img_size_rgba, activation='relu'))

model.add(MaxPooling2D(pool_size=(2,2),strides=2))

model.add(Flatten())

model.add(Dropout(0.5))

model.add(Dense(256, activation='relu'))

model.add(Dense(len(classes), activation='softmax'))

opt = optimizers.Adam(lr=0.001)

model.compile(loss='binary_crossentropy',
              optimizer=opt,
              metrics=['accuracy'])

print(model.summary())

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d_1 (Conv2D)            (None, 32, 32, 32)        1184      
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 16, 16, 32)        0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 16, 16, 64)        18496     
_________________________________________________________________
max_pooling2d_2 (MaxPooling2 (None, 8, 8, 64)          0         
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 8, 8, 128)         73856     
_________________________________________________________________
max_pooling2d_3 (MaxPooling2 (None, 4, 4, 128)         0         
_________________________________________________________________
flatten_1 (Flatten)          (None, 2048)             

In [7]:
kf = KFold(n_splits=10, shuffle=False)
accuracies = []

In [8]:
for train_index, val_index in kf.split(X, Y):
    X_train, X_val = X[train_index], X[val_index]
    Y_train, Y_val = Y[train_index], Y[val_index]
    transfer_all_class(validation_dir_name,train_dir_name,1.0,classes)
    for index in range(len(X_val)):
        class_label=''
        if(Y_val[index]==0):
            class_label=classes[0]
        else:
            class_label=classes[1]  
        #Then, copy the validation images to the validation folder
        shutil.move(train_dir_name+"/"+class_label+'/'+X_val[index], 
                    validation_dir_name+"/"+class_label+'/'+X_val[index])
        
    batch_size = 256
    epoch=100
    datagen = ImageDataGenerator(rescale=1./255)

    train_generator = datagen.flow_from_directory(
        train_dir_name,
        target_size=img_size,
        color_mode='rgba',
        batch_size=batch_size,
        class_mode='categorical')

    validation_generator = datagen.flow_from_directory(
        validation_dir_name,
        target_size=img_size,
        color_mode='rgba',
        batch_size=batch_size,
        class_mode=None)
        
    history=model.fit_generator(train_generator, 
                        epochs=epoch)
        
    predictions = model.predict_generator(validation_generator, verbose=1)
    y_predictions = np.argmax(predictions, axis=1)
    y_true = validation_generator.classes
    accuracy=accuracy_score(y_true, y_predictions)
    accuracies.append(accuracy)
    print(accuracy)

Found 13547 images belonging to 2 classes.
Found 1506 images belonging to 2 classes.
Epoch 1/100
53/53 [==============================] - 9s 162ms/step - loss: 0.6933 - accuracy: 0.5336

In [9]:
np.average(accuracies)

0.9222189867330235

In [10]:
test_generator = datagen.flow_from_directory(
    test_dir_name,
    target_size=img_size,
    color_mode='rgba',
    batch_size=batch_size,
    class_mode='categorical')

Found 1671 images belonging to 2 classes.


In [12]:
loss, acc = model.evaluate_generator(test_generator)
acc

0.7289048433303833